In [1]:
import pandas as pd
import numpy as np
import itertools 
from fuzzywuzzy import fuzz

#dataframes to traverse on txt files
global df1,df2,df3,df4
Path = "/home/anjali/Desktop/DTC_CHANGES"
df1 = pd.read_csv(f'{Path}/routes.txt',delimiter = ",",dtype={'route_short_name':'float64','route_long_name':'object','route_type':'int','route_id':'int','agency_id':'object'})
df2 = pd.read_csv(f'{Path}/trips.txt', delimiter = ",",dtype = {'route_id': 'int64', 'service_id': 'int64', 'trip_id': 'O', 'shape_id': 'float64'})
df3 = pd.read_csv(f'{Path}/stop_times.txt',delimiter = ",",dtype = {'trip_id': 'O', 'arrival_time': 'O', 'departure_time': 'O', 'stop_id': 'O', 'stop_sequence': 'int'})
df4 = pd.read_csv(f'{Path}/stops.txt', delimiter=",",dtype={'stop_id':'object','stop_code':'object','stop_name':'O','stop_lat':'float64','stop_lon':'float64'})

#function to match 2 given string using fuzzywuzzy library
def checkString(str1,str2):
    #token_set_ratio ignores upper and lower case letters , token_sort_ratio ignore order of letters
    #if(fuzz.token_set_ratio(str1,str2) > 80):
    #WRatio handles lower and upper cases and some other parameters too
    if(fuzz.WRatio(str1,str2) > 80 or fuzz.token_set_ratio(str1,str2) > 80 or fuzz.token_sort_ratio(str1,str2) > 80):
        return True
    else:
        return False

#function to WRtaio % by fuzzywuzzy
def findperc1(str1,str2):
    return fuzz.WRatio(str1,str2)

#function to token_sort_ratio % by fuzzywuzzy
def findperc2(str1,str2):
    return fuzz.token_sort_ratio(str1,str2)

    
#function to match 2 given strings (ignoring whitespace,special characters,upper&lower case)
def Stringcheck(str1,str2):
    disallowed_characters = [".",'',"!","-"," ","@",""]
    m = str1.lower()
    n = str2.lower()
    for character in disallowed_characters:
        m = m.replace(character, "")
        n = n.replace(character, "")
    if m ==n:
        return True
    else:
        return False

        
#traversing routes.txt file to get route_id corresponding to the route name
def routes_txt(route_lname):
    t  = route_lname+"_DTC"
    if t in df1.values:
        routeid = df1[(df1['route_long_name'] == t) & (df1['agency_id']=='DTC')]['route_id'].item()
        k = trip_txt(routeid)
        return k
    else:
        return []

#traversing trip.txt file to fing trip id corresponding to the route_id
def trip_txt(routeid):
    tripid = df2.loc[(df2['route_id']==routeid),'trip_id'].unique()[0]
    z = stop_times_txt(tripid)
    return z

#traversing stop_times.txt file to find count all stop counts correspoding to the trip_id
def stop_times_txt(tripid):
    old_stops = []
    stopid = df3.loc[df3['trip_id']==tripid,'stop_id'].tolist()
    for x in stopid:
        p = stop_txt(x)
        old_stops.append(p)      
    return old_stops

#traversing stop.txt file to find all stop names correspoding to the trip_id
def stop_txt(stopid):
    stopname = df4.loc[df4['stop_id']== stopid,'stop_name'].tolist()
    return stopname[0]
    

#function to match all stops sequences in old and new data for all routes
def MatchDataSequence():
    
    #extracting names of all routes in New DTC Data from DTC_NewData txt file
    df = pd.read_csv('/home/anjali/Desktop/DTC_CHANGES/DTC_NewData.txt', delimiter = ",")
    for ind in df.index:
            filenames = df['DTC_routes'][ind]
            fileName , separator , extension = filenames.partition('.')
            
            #passing the route name to routes_txt , storing old data stops in a list old_data
            old_data = routes_txt(fileName)#list of old stops
            
            #reading new dtc data from .csv files
            dataf = pd.read_csv(f'/home/anjali/Desktop/NewDTCdata/{filenames}',delimiter = ",")
            
            if('Stops_up' in dataf.columns):
                new_data = dataf['Stops_up'].tolist()#list of new stops
            else:
                new_data = dataf['Stops_down'].tolist()#list of new stops
            
            #string matching for old and new stops
            print(f"Route : {fileName}")
            print(f"Total stops in old data : {len(old_data)}")
            print(f"Total stops in new data : {len(new_data)}")
            
            #traversing old_data list of old DTC stops and finding corresponding stops in new_data list 
            new = [] #list to store final output of sequence matching
            if(len(old_data) and len(new_data)):
                i = 0
                #traversing complete list 1
                while(i < len(old_data)):
                    str1 = old_data[i]
                    str2 = ""
                    if( i < len(new_data)):
                        str2 = new_data[i]
                        
                    #if strings did matched for same index , store in output list
                    if (str1 == str2):
                         new.append("Match")
                    
                    #checking str1 and str2 by fuzzywuzzy string matching
                    elif (Stringcheck(str1,str2) == True):
                        new.append("Match")

                    elif (checkString(str1,str2) == True):
                        
                        if(findperc1(str1,str2) > 90 and findperc2(str1,str2) > 70):
                            new.append("Match")
                            
                        elif (findperc1(str1,str2) > 80 and findperc2(str1,str2) > 50):
                            new.append("Slightly match")
                            
                        else:
                            new.append("Not matched")
                
                    #when strings did not match for same index ,checking for all other indexes in new_data list
                    else:
                        j = 0
                        flag = True
                        while( j < len(new_data) and flag==True):
                            if (Stringcheck(str1,new_data[j]) == True):
                                new.append(f'Match at {j+1} in new_data list')
                                flag = False
                                break
                            else:
                                j += 1
                        if(flag == True and j == len(new_data)):
                            new.append("Not matched")
                    i += 1
                
                #creating a dataframe with the final output list
                a = {'OLD_STOPS':old_data, 'NEW_STOPS':new_data, 'OUTPUT':new}
               

            #if old_data list or new_data list is empty , return 0 stops for correspoding route
            else:
                if len(old_data) == 0:
                    print("No stops in Old data")
                    list1 = [None] * len(new_data)
                    a = {'OLD_STOPS':list1, 'NEW_STOPS':new_data}

                    
                else:
                    print("No stops in New data")
                    list1 = [None] * len(old_data)
                    a = {'OLD_STOPS':old_data, 'NEW_STOPS':list1}
            
            dframe = pd.DataFrame.from_dict(a, orient='index').T
            dframe.index = np.arange(1, len(dframe) + 1)
            print(dframe.to_string())
                
            #stroring the dataframe in a .csv file for all routes
            dframe.to_csv(f'/home/anjali/Desktop/SequenceMatching/{filenames}')

            
#calling the function for sequence matching        
MatchDataSequence()

Route : 0114(NS)DOWN
Total stops in old data : 0
Total stops in new data : 68
No stops in Old data
   OLD_STOPS                          NEW_STOPS
1       None                         Qutab Garh
2       None                           Jat Khor
3       None                       Punjab Khore
4       None                    Tatesar Gurukul
5       None                    Tatesar Village
6       None                              Jonti
7       None                    Jounti Crossing
8       None               S. Vivekanand School
9       None                            Lad Pur
10      None                    Nirmal Hospital
11      None                   Kanjhawala Chowk
12      None                     Shivam Plywood
13      None          Rupali Enclave RS Satsang
14      None             Shiv Vihar Bheem Chowk
15      None                        Desu Office
16      None                             Karala
17      None                      Karala School
18      None                         

Route : 0118EXT(NS)UP
Total stops in old data : 39
Total stops in new data : 39
                           OLD_STOPS                         NEW_STOPS                        OUTPUT
1                 Mayur Vihar Ph-III       Mayur Vihar Ph III Terminal                Slightly match
2                 Mayur Vihar Ph-III  Khoda Colony (Mayur Vihar Ph III                Slightly match
3                          CRPF Camp                         CRPF Camp                         Match
4     Mayur Vihar Phase III A1 Block               Mayur Vihar Pkt A I                Slightly match
5               Bharti Public School              Bharti Public School                         Match
6            New Kondali A1 Crossing                       New Kondali                Slightly match
7     Mayur vihar Phase-III Crossing        Mayur Vihar Phase III xing                Slightly match
8   Vasundhra Enclave Sports Complex  Vasundhra Enclave Sports Complex                         Match
9          

Route : 0131(NS)UP
Total stops in old data : 59
Total stops in new data : 59
                                       OLD_STOPS                       NEW_STOPS                        OUTPUT
1                      Old Delhi Railway Station       Old Delhi Railway Station                         Match
2                                            GPO                      GPO K.Gate                   Not matched
3   Guru Govind Singh University (Kashmere Gate)               GGS IP University                Slightly match
4                             ISBT Kashmere Gate                     ISBT K.Gate                Slightly match
5                              Tees Hazari Court                Tis Hazari Court                         Match
6                            St Stephen Hospital              St.Stephen's Hosp.                Slightly match
7                   Ice Factory (Roshanara Road)                     Ice Factory                Slightly match
8                                  

Route : 0205(NS)UP
Total stops in old data : 37
Total stops in new data : 37
                                       OLD_STOPS                  NEW_STOPS          OUTPUT
1                      Old Delhi Railway Station  Old Delhi Railway Station           Match
2                                            GPO                 GPO K.Gate     Not matched
3   Guru Govind Singh University (Kashmere Gate)          GGS IP University  Slightly match
4                             ISBT Kashmere Gate                ISBT K.Gate  Slightly match
5                            Isbt Nityanand Marg        ISBT Nityanand Marg           Match
6                                   Shastri Park  Shashtri Park Metro Depot  Slightly match
7                              Shyam Giri Mandir          Shyam Giri Mandir           Match
8                                   Shastri Park              Shashtri Park           Match
9                                     Dharampura                Dharam Pura           Match
10 

Route : 0236(NS)UP
Total stops in old data : 55
Total stops in new data : 55
                                         OLD_STOPS                      NEW_STOPS          OUTPUT
1                        Anand Vihar ISBT Terminal               ISBT Anand Vihar  Slightly match
2                             Ram Prastha Crossing           Ram Prastha Crossing           Match
3                               Ram Prastha Temple                     Ramprashta     Not matched
4                                      Surya Nagar                    Surya Nagar           Match
5                                   Shahdra Border                 Shahdra Border           Match
6                                     Jhilmil Xing                  Jhilmil X ing           Match
7                           Dilshad Garden GT Road         Dilshad Garden GT Road           Match
8                               Telephone Exchange             Telephone Exchange           Match
9                    Mansarovar Park Metr

...

Route : RL-77BDOWN
Total stops in old data : 50
Total stops in new data : 50
                                 OLD_STOPS                                  NEW_STOPS          OUTPUT
1   Dwarka More Metro Station (Sewak Park)                  Dwarka More Metro Station           Match
2            Netaji Subhash Inst of Techni             Netaji Subhash Inst of Technic           Match
3                            Dwarka Sec 13                              Dwarka Sec-13           Match
4                           Dwarka Sec 3/4                        Dwarka Sec-3/4 Xing           Match
5                            Matiyala Xing                          Matiyala Crossing     Not matched
6                              Madhu Vihar  Delhi Pub. School (Matiala) / Madhu Vihar     Not matched
7                                Raja Puri                                  Raja Puri           Match
8                              Madhu Vihar                                Madhu Vihar           Match
9    

Route : RL-77DOWN
Total stops in old data : 43
Total stops in new data : 43
                              OLD_STOPS                            NEW_STOPS          OUTPUT
1                      Mangla Puri Xing                          MANGLA PURI           Match
2                           Mangla Puri                     MANGLA PURI XING           Match
3                   Palam Health Centre                        HEALTH CENTER     Not matched
4           Sulabh International Centre                               SULABH     Not matched
5                  Mahaveer Enclave III                     MAHAVIR ENCLAVE      Not matched
6                         Dashrath Puri                        DASHRATH PURI           Match
7      Vijay Enclave (Palam-Dabri Road)                        VIJAY ENCLAVE  Slightly match
8                         Dabri Village                        DABRI VILLAGE           Match
9                            Dabri Xing                           Dabri Xing           

Route : RL-77EXTUP
Total stops in old data : 50
Total stops in new data : 50
                             OLD_STOPS                            NEW_STOPS          OUTPUT
1     New Delhi Railway Station Gate 2  New Delhi Railway Station Gate No.2           Match
2                 Bakhtawar Pur School                         Shivaji Park     Not matched
3                          Super Bazar                          Super Bazar           Match
4                                Regal                                Regal           Match
5                       Tibiya College                      P.S. Parliament     Not matched
6                          Patel Chowk                          Patel Chowk           Match
7               Gurudwara Bangla Sahib               Gurudwara Bangla Sahib           Match
8                                 NDPO                                 NDPO           Match
9    Kendriya Terminal (Pt. Pant Marg)                    Kendriya Terminal  Slightly match
10 

Route : TMS(+)UP
Total stops in old data : 67
Total stops in new data : 68
                                      OLD_STOPS                              NEW_STOPS                        OUTPUT
1                         Punjabi Bagh Terminal                Punjabi Bagh Terminal                           Match
2                         Shakurpur Shiv Mandir                 Shakur Pur Shiv Mandir                         Match
3                     Britannia Chowk Shakurpur                               Britania                   Not matched
4                  Telephone Exchange Shakurpur                     Telephone Exchange                Slightly match
5                  Wazirpur DTC Depot Ring Road                         Wazirpur Depot                Slightly match
6          Wazirpur Depot / Subhash Place Depot                   Subhash Place Depot                 Slightly match
7                                Prem Bari Pull                         Prem Bari Pull                    

Route : WESTDELHIMUDRIKA(+)UP
Total stops in old data : 68
Total stops in new data : 68
                                 OLD_STOPS                      NEW_STOPS                        OUTPUT
1                              Madhu Vihar                    Madhu Vihar                         Match
2                                Raja Puri                      Raja Puri                         Match
3                             DPS Matiyala   Delhi Pub. School (Matiala)                    Not matched
4                             DPS Matiyala              Matiyala Crossing                   Not matched
5                           Dwarka Sec 3-4           Dwarka Sec 3/4 X-ing                         Match
6                            Dwarka Sec 13                  Dwarka Sec 13                         Match
7   Netaji Subhash Institute of Technology  Netaji Subhash Inst of Techni                Slightly match
8   Dwarka More Metro Station (Sewak Park)      Dwarka More Metro Station       